In [1]:
import requests
from lxml import etree
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.firefox.service import Service
from selenium.webdriver.firefox.options import Options
from time import sleep


options = Options()
options.add_argument("--headless")
service = Service(executable_path=r".\geckodriver.exe")
browser = webdriver.Firefox(service=service, options=options)
browser.get("https://store.steampowered.com/charts/topselling/RU")

sleep(15)

raw_html = browser.page_source
raw_html

'<html lang="en"><head>\n<meta charset="UTF-8">\n<meta name="viewport" content="width=device-width, initial-scale=1.0">\n<title>SteamDB</title>\n<meta name="theme-color" content="#1B2838">\n<style>:root{--navbar-height:48px;--body-bg-color:#161920;--body-color:#ddd;--contrast-color:#fff;--muted-bg-color:#213145;--muted-color:#999;--border-color:#394960;--border-color-2:#1f2733;--link-color:#00aff4;--link-color-hover:#0095ff;--bg-green:#030;--bg-blue:#00174d;--state-text-color:#111;--state-owned:89 185 70;--state-wished:102 148 255;--state-watched:87 132 168;--state-followed:211 222 234;--state-cart:247 203 8;--state-ignored:191 191 191;--tooltip-bg:hsla(0,0%,100%,.8);--tooltip-green:#577c27;color-scheme:dark;scrollbar-color:var(--border-color) var(--body-bg-color);-moz-tab-size:4;tab-size:4}html{-webkit-text-size-adjust:none;text-size-adjust:none;box-sizing:border-box;overflow-y:scroll;scroll-padding-top:calc(var(--navbar-height) + 15px)}*,:after,:before{box-sizing:inherit}body{backgro

In [86]:
soup = BeautifulSoup(raw_html, "html.parser")
games = soup.find_all("tr", class_="weeklytopsellers_TableRow_2-RN6")

In [87]:
import pandas as pd


df = pd.DataFrame(columns=["rating", "name", "price", "has_sale", "sale", "original_price", "is_new", "delta", "weeks_in_top"])

In [88]:
for game in games:
    rating = game.find("td", class_="weeklytopsellers_RankCell_34h48").text
    name = game.find("div", class_="weeklytopsellers_GameName_1n_4-").text
    price = game.find_all("div", class_="salepreviewwidgets_StoreSalePriceBox_Wh0L8")[-1].text

    sale_box = game.find("div", class_="salepreviewwidgets_StoreSaleDiscountBox_2fpFv")
    has_sale = int(not (sale_box is None))
    
    if has_sale:
        sale = sale_box.text
        original_price = game.find("div", class_="salepreviewwidgets_StoreOriginalPrice_1EKGZ").text
    else:
        sale = 0
        original_price = price

    raw_delta = game.find_all("div", class_="weeklytopsellers_Tooltip_2OA1J")[0].text
    is_new = int(raw_delta == "Новинка")
    delta = int(raw_delta.replace("Новинка", "0").replace("▲ ", "").replace("▼ ", "-"))
    weeks_in_top = int(game.find_all("div", class_="weeklytopsellers_Tooltip_2OA1J")[1].text)

    df.loc[len(df.index)] = (rating, name, price, has_sale, sale, original_price, is_new, delta, weeks_in_top)

df.price = df.price.apply(lambda x: float(x.replace("Бесплатно", "0").replace(" руб", "").replace(",", ".")))
df.original_price = df.original_price.apply(lambda x: float(x.replace("Бесплатно", "0").replace(" руб", "").replace(",", ".")))

# df.to_csv("steam_top_100.csv")
df

rating                     name    price  has_sale  sale  original_price  \
0       1                   Dota 2     0.00         0     0             0.0   
1       2                     Rust   550.00         1  -50%          1100.0   
2       3         Counter-Strike 2     0.00         0     0             0.0   
3       4           Lethal Company   385.00         0     0           385.0   
4       5           Hunt: Showdown   472.15         1  -65%          1349.0   
..    ...                      ...      ...       ...   ...             ...   
95     96           Death Must Die   280.00         0     0           280.0   
96     97         Shadows of Doubt   568.00         1  -20%           710.0   
97     98  Rust - Instruments Pack   140.00         1  -50%           280.0   
98     99               Remnant II  2869.00         0     0          2869.0   
99    100               The Forest   435.00         0     0           435.0   

    is_new  delta  weeks_in_top  
0        0      1           602  
1        0      2           522  
2        0     -2           592  
3        0     -1             6  
4        0      8           160  
..     ...    ...           ...  
95       0    -26             2  
96       1      0             1  
97       1      0             1  
98       0    -68            27  
99       0    -59           103  

[100 rows x 9 columns]

In [102]:
browser.get("https://store.steampowered.com/search/?filter=topsellers")

sleep(15)

for i in range(60):
    browser.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    sleep(1)

raw_html = browser.page_source
raw_html

'<html class=" responsive" lang="ru"><head>\n\t<meta http-equiv="Content-Type" content="text/html; charset=UTF-8">\n\t\t\t<meta name="viewport" content="width=device-width,initial-scale=1">\n\t\t<meta name="theme-color" content="#171a21">\n\t\t<title>Поиск Steam</title>\n\t<link rel="shortcut icon" href="/favicon.ico" type="image/x-icon">\n\n\t\n\t\n\t<link href="https://store.cloudflare.steamstatic.com/public/shared/css/motiva_sans.css?v=2C1Oh9QFVTyK&amp;l=russian&amp;_cdn=cloudflare" rel="stylesheet" type="text/css">\n<link href="https://store.cloudflare.steamstatic.com/public/shared/css/shared_global.css?v=7sR4EhV3nKzm&amp;l=russian&amp;_cdn=cloudflare" rel="stylesheet" type="text/css">\n<link href="https://store.cloudflare.steamstatic.com/public/shared/css/buttons.css?v=hFJKQ6HV7IKT&amp;l=russian&amp;_cdn=cloudflare" rel="stylesheet" type="text/css">\n<link href="https://store.cloudflare.steamstatic.com/public/css/v6/store.css?v=ncKRKw_W8xuN&amp;l=russian&amp;_cdn=cloudflare" rel="

In [103]:
soup = BeautifulSoup(raw_html, "html.parser")
games = soup.find_all(class_="responsive_search_name_combined")
len(games)

2950

In [123]:
df = pd.DataFrame(columns=["rating", "name", "release_date", "has_sale", "sale", "final_price", "original_price"])

In [124]:
rating = 1
for game in games:
    name = game.find(class_="title").text
    release_date = game.find(class_="responsive_secondrow").text.strip()

    sale_box = game.find(class_="discount_pct")
    has_sale = not (sale_box is None)

    if has_sale:
        sale = sale_box.text
    else:
        sale = "0"

    final_price_box = game.find(class_="discount_final_price")
    if not (final_price_box is None):
        final_price = final_price_box.text
    else:
        final_price = 0

    if has_sale:
        original_price = game.find(class_="discount_original_price").text
    else:
        original_price = final_price
    
    # print(rating, name, release_date, has_sale, sale, final_price, original_price)

    df.loc[len(df.index)] = (rating, name, release_date, int(has_sale), sale, final_price, original_price)

    rating += 1

In [138]:
from datetime import datetime


def change_date(x):
    x = x.replace(".", "")
    x = x.replace("марта", "Mar")
    x = x.replace("янв", "Jan")
    x = x.replace("дек", "Dec")
    x = x.replace("мар", "Mar")
    x = x.replace("апр", "Apr")
    x = x.replace("мая", "May")
    x = x.replace("июн", "Jun")
    x = x.replace("июл", "Jul")
    x = x.replace("авг", "Aug")
    x = x.replace("сен", "Sen")
    x = x.replace("окт", "Oct")
    x = x.replace("ноя", "Nov")
    x = x.replace("фев", "Feb")

    try:
        return datetime.strptime(x, "%d %b %Y").strftime("%Y-%m-%d")
    except:
        return "no date"

df.release_date = df.release_date.apply(change_date)
df

rating                                    name release_date  has_sale  \
0          1                                  Dota 2   2013-01-09         0   
1          2                                    Rust   2018-01-08         1   
2          3                        Counter-Strike 2   2012-01-21         0   
3          4                          Hunt: Showdown   2019-01-27         1   
4          5                         Baldur's Gate 3   2023-01-03         0   
...      ...                                     ...          ...       ...   
2945    2946                           Event Horizon   2018-01-20         0   
2946    2947  Surviving Mars: In-Dome Buildings Pack   2021-01-15         0   
2947    2948                             Darksiders™   2010-01-24         0   
2948    2949        Dungeons 3 - A Multitude of Maps   2020-01-21         0   
2949    2950                      Bugsnax Soundtrack   2022-01-28         0   

      sale final_price original_price  
0        0   Бесплатно      Бесплатно  
1     -50%     550 руб       1100 руб  
2        0   Бесплатно      Бесплатно  
3     -65%  472,15 руб       1349 руб  
4        0    1999 руб       1999 руб  
...    ...         ...            ...  
2945     0     149 руб        149 руб  
2946     0     133 руб        133 руб  
2947     0           0              0  
2948     0     299 руб        299 руб  
2949     0     259 руб        259 руб  

[2950 rows x 7 columns]